In addition to the original script, 2_generate_TP, this script does a blast search of selected_tp_genes against temp_neg_genomes and filters out all genomes that have a hit. In addition to 2.1_generate_TP, this script also does an hmm search, using an alignment of selected_tp_genes as query against negative genomes. It combines results of blast and hmm searches and removes all samples with hits from the pool of neg_genomes to choose from. One further parameter is required to specify an hmm evalue cutoff for samples to remove. Ideally, this would be 0, but I decided to keep a cutoff, as the original negative genomes from the sugimoto paper also have positive hits for an oxyN hmm.


This script generates the 2 remaining files required for input:
- True positive genes (nucleotide fasta)
- protein alignment (amino acid fasta)
IMPORTANTLY, these 2 files are created from non-overlapping sequences!


And also moves the corresponding files to new directories so that coverage tables can be generated from them.

In the first cell specify:
- BGC type (This name must stay constant throughout the scripts)
- select_neg_genomes, i.e. the amount of negative genomes to be transferred to the neg_genomes directory
- select_pos_genomes, i.e. the amount of positive genomes to be transferred to the pos_genomes directory and to generate the tp_genes file from (the surplus amount will be used to generate the protein alignment from)
- pos_isolation_source_filter, if these terms are found in the isolation_source column of the positive samples in the summary file, they will be scored higher in a scoring column, i.e. samples from a known and desired isolation source will be used preferentially.
- neg_isolation_source_filter, accordingly
- avoid_list. These terms are scored with a 0, end at the bottom of the table, and will be picked last. This is useful when an uncommon gene is searched for and more, and/or more tenuous isolation sources have been allowed during download. These are generally words that contain one of the search terms, e.g. 'sea' in 'diseased'.

Modify in such a way that TP genes are used as query against all individual negative genomes. Negative genomes are only moved from temp directory to neg_genomes directory if the blast search comes back negative

In [1]:
BGC_type = 'RTX_toxin_acyltransferase_combined'
select_neg_genomes = 141
select_pos_genomes = 10
hmm_evalue_cutoff = 3

avoid_list = ['', 'diseased', 'isolation_source not annotated', 'mice', 'spice', 'septicemic', 'septicemia', 'research', 'crevice']
#these are identical to first script, but don't have to be
pos_isolation_source_filter =  ['marine', 'sea', 'sponge', 'ocean', 'porifera', 'seafloor','sediment', 'water', 'tidal', 'coral', 'reef', 'coast', 'ship', 'fish', 'aquaculture', 'atlantic', 'pacific', 'mediterranean', 'baltic', 'pond', 'river', 'carribean', 'lake', 'fjord', 'marina', 'hydro', 'algal', 'algae', 'clam', 'shell', 'mussel']
neg_isolation_source_filter = ['marine', 'sea', 'sponge', 'ocean', 'porifera', 'seafloor', 'sediment', 'water', 'tidal', 'coral', 'reef', 'coast', 'ship', 'fish', 'aquaculture', 'atlantic', 'pacific', 'mediterranean', 'baltic', 'pond', 'river', 'ice', 'carribean', 'lake', 'fjord', 'marina', 'hydro', 'algal', 'algae', 'clam', 'shell', 'mussel']

In [2]:
import os
from os import listdir, mkdir
from os.path import isfile, join
from pathlib import Path
import pandas as pd
from pandas.errors import EmptyDataError
import warnings

In [3]:
def makedir(dirpath):
    if os.path.isdir(dirpath):
        print(dirpath,'exists already')
    else:
        print('Making', dirpath)    
        os.mkdir(dirpath)

        
# Defining paths for required directory structure for input and output files relative to parent directory
#parent_dir='/media/manu/RiPP_Prioritiser/'
#will make directories relative to the path the notebook was opened in
parent_dir= !echo $(pwd)
BGC_path=os.path.join(parent_dir[0], BGC_type)
neg_genomes_path=os.path.join(BGC_path, 'base_genomes/temp_neg_genomes')
pos_genomes_path=os.path.join(BGC_path, 'base_genomes/temp_pos_genomes')
output_neg_path=os.path.join(BGC_path, 'base_genomes/neg_genomes')
output_pos_path=os.path.join(BGC_path, 'base_genomes/pos_genomes')
#qc-paths.
quality_control_path=os.path.join(BGC_path, 'base_genomes/quality_control')
neg_blast_path=os.path.join(quality_control_path, 'neg_blast')
neg_blast_db_path=os.path.join(neg_blast_path, 'databases')
neg_blast_results_path=os.path.join(neg_blast_path, 'outfiles')
pos_blast_path=os.path.join(quality_control_path, 'pos_blast')
pos_blast_db_path=os.path.join(pos_blast_path, 'databases')
pos_blast_results_path=os.path.join(pos_blast_path, 'results')
neg_hmm_path=os.path.join(quality_control_path, 'neg_hmm')
neg_hmm_db_path=os.path.join(neg_hmm_path, 'queries')
neg_hmm_results_path=os.path.join(neg_hmm_path, 'outfiles')
pos_hmm_path=os.path.join(quality_control_path, 'pos_hmm')
pos_hmm_db_path=os.path.join(pos_hmm_path, 'databases')
pos_hmm_results_path=os.path.join(pos_hmm_path, 'results')

# made directories manually. remove or comment after running.
#validation_pos_genomes_path=os.path.join(BGC_path, 'base_genomes/validation_pos_genomes')
#validation_coverage_table_path=os.path.join(BGC_path, 'validation_coverage_tables')

# Calling function to make directories if they don't exist yet
makedir(output_neg_path)
makedir(output_pos_path)
makedir(quality_control_path)
makedir(neg_blast_path)
makedir(neg_blast_db_path)
makedir(neg_blast_results_path)
makedir(pos_blast_path)
makedir(pos_blast_db_path)
makedir(pos_blast_results_path)
makedir(neg_hmm_path)
makedir(neg_hmm_db_path)
makedir(neg_hmm_results_path)
makedir(pos_hmm_path)
makedir(pos_hmm_db_path)
makedir(pos_hmm_results_path)

#makedir(validation_pos_genomes_path)

os.chdir(BGC_path)

Making /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
Making /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes
Making /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control
Making /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast
Making /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases
Making /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/outfiles
Making /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_blast
Making /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_blast/databases
Making /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_blast/results
Making /med

In [4]:
# Generating a report file for this script
with open(BGC_path+'/'+'report_2_generate_tp.txt', 'w') as f:
    f.write('Output directory is: '+BGC_path+'\n')
    f.write('\nBGC_type = '+BGC_type)
    f.write('\nselect_neg_genomes = '+str(select_neg_genomes))
    f.write('\nselect_pos_genomes = '+str(select_pos_genomes))
    f.write('\nhmm_evalue_cutoff = '+str(hmm_evalue_cutoff))
    f.write('\navoid_list = '+str(avoid_list))
    f.write('\nneg_isolation_source_filter = '+str(neg_isolation_source_filter))
    f.write('\npos_isolation_source_filter = '+str(pos_isolation_source_filter)+'\n')

In [5]:
# load summary table into data frame () output from 1.)
summary_file = pd.read_csv('summary.tsv', sep='\t')

Change order of tables to prioritize samples that have an isolation source

In [6]:
warnings.filterwarnings('ignore')

#filter positives and drop all duplicate protein sequences originating from different organisms
pos_mask = (summary_file['dir'] == '+')
pos_df = summary_file[pos_mask]

#filter negatives
neg_mask = (summary_file['dir'] == '-')
neg_df = summary_file[neg_mask]

#scoring words in isolation source so as to preferentially pick samples with chosen isolation sources
# I think the sorting is buggy when there are conflicts between pos and neg isolation_source_filter words
# E.g. septicemic (negative) contains 'ice' (positive)

def custom_sorting(source,isolation_source_filter):
    score = 1
    if isolation_source_filter=='pos':
        for word in pos_isolation_source_filter:
            if word in source:
                score +=1
        for word in avoid_list:
            if source == word:
                score=0
    elif isolation_source_filter=='neg':
        for word in neg_isolation_source_filter:
            if word in source:
                score +=1
        for word in avoid_list:
            if source == word:
                score=0
    return score


pos_df['scoring_column'] = pos_df.apply(lambda x: custom_sorting(x['isolation_source'],'pos'),axis=1)
neg_df['scoring_column'] = neg_df.apply(lambda x: custom_sorting(x['isolation_source'],'neg'),axis=1)

# Changed keep parameter to 'first' from False
pos_df.drop_duplicates(subset='protein_id', keep='first', inplace=True)

pos_df.sort_values(by=['scoring_column'], axis=0, ascending=False, inplace=True)
neg_df.sort_values(by=['scoring_column'], axis=0, ascending=False, inplace=True)
# print(sorted(list(set(list(pos_df.loc[:,'protein_id'])))))

In [7]:
#Split positive genomes into 2 bins, one goes towards tp-genes and is the pos-genomes used for synthesising metagenomes
#the other one constitutes a source of protein sequences for alignment as an input file
#(removed the latter functionality and used pfam alignments of the protein instead)

# Genomes selected in such a way that they are from the top of the pre-sorted pos_df
unique_pos_df = pos_df.drop_duplicates(subset='assembly', inplace=False)
selected_tp_genomes = list(unique_pos_df.iloc[:,1])[0:select_pos_genomes]
remaining_pos_genomes = list(unique_pos_df.iloc[:,1])[select_pos_genomes:]

with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\nselected_tp_genomes are:\n')
    f.write(str(selected_tp_genomes)+'\n')

#select genomes and isolate GCF number from them, move selected tp genomes to final pos_genomes directory
for genome in selected_tp_genomes:
    print('moving positive', genome, 'to', output_pos_path)
    !mv "{pos_genomes_path}"/"{genome}"* "{output_pos_path}"
    
#generate dataframe containing all tp-genomes and all the tp-genes contained in it
filtered_pos_df = pos_df[pos_df['assembly'].isin(selected_tp_genomes)]
remaining_pos_df = pos_df[~pos_df['assembly'].isin(selected_tp_genomes)]

#isolate all the headers and transfer them to the selected_tp_genes file
full_header_list = []
for i in range(0,len(filtered_pos_df)):
    full_header=str('>')+filtered_pos_df.iloc[i,1]+str('_')+filtered_pos_df.iloc[i,3]+str('_')+filtered_pos_df.iloc[i,5]
    full_header_list.append(full_header)

# generate fasta file with selected tp genes found in the selected genomes
print('generating selected_tp_genes.fasta')
with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\nselected_tp_genes in positive genomes are:\n')
tp_gene_counter=0
with open(BGC_path+'/'+BGC_type+'_tp_genes.fasta') as fh:
    lines=fh.readlines()
    for i in range(0,len(lines)):
        for j in range(0,len(full_header_list)):
            if full_header_list[j] in lines[i]:
                tp_gene_counter+=1
                with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
                    f.write(lines[i][1:-1]+'\n')
                with open(BGC_path+'/'+BGC_type+'_selected_tp_genes.fasta', 'a') as outfile:
                    outfile.write(lines[i]+lines[i+1])    
with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\n'+str(len(selected_tp_genomes))+' unique genomes with '+ str(tp_gene_counter)+' unique tp genes.\n\n')
                    
                    
# transfer all amino acid sequences that are not part of the tp-genomes to a fasta file
print('generating selected_tp_aa.fasta')
with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\nremaining samples are:\n')
tp_aa_counter = 0
with open(BGC_path+'/'+BGC_type+'_selected_tp_aa.fasta', 'a') as outfile:
    for i in range(0,len(remaining_pos_df)):
        tp_aa_counter+=1
        fasta_header=str('>')+remaining_pos_df.iloc[i,1]+str('_')+remaining_pos_df.iloc[i,3]+str('_')+remaining_pos_df.iloc[i,5]+'\n'
        sequence = remaining_pos_df.iloc[i,6][2:-2]+'\n'
        with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
            f.write(fasta_header[1:-1]+'\n')
        outfile.write(fasta_header)
        outfile.write(sequence)
with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\n'+str(len(remaining_pos_genomes))+' unique genomes with '+ str(tp_aa_counter)+' unique aa sequences.\n\n')

    
print('Done')

moving positive GCF_012275045.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes
moving positive GCF_013357805.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes
moving positive GCF_013357665.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes
moving positive GCF_013357885.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes
moving positive GCF_002119525.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes
moving positive GCF_013357825.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes
moving positive GCF_008369605.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes
moving positive GCF_001455365.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes
moving p

In [8]:
# move 10 more pos_genomes to validation_pos_genomes
#unique_pos_df = pos_df.drop_duplicates(subset='assembly', inplace=False)
#selected_tp_genomes = list(unique_pos_df.iloc[:,1])[0:select_pos_genomes]
#validation_tp_genomes=list(unique_pos_df.iloc[:,1])[select_pos_genomes:select_pos_genomes+10]

#select genomes and isolate GCF number from them, move selected tp genomes to final pos_genomes directory
#for genome in validation_tp_genomes:
#    print('moving positive', genome, 'to', validation_pos_genomes_path)
#    !mv "{pos_genomes_path}"/"{genome}"* "{validation_pos_genomes_path}"

In [9]:
# To confirm, run blast on all samples selected as validation pos genomes

# makes blast databases of all individual neg genomes (easier to keep track of accession numbers than when combining)
#for genomes in validation_tp_genomes:
#    !makeblastdb -in "{validation_tp_genomes}"/"{genomes}"* -dbtype nucl -out "{pos_blast_db_path}"/"{genomes}"_db

#for genomes in selected_tp_genomes:
#    !blastn -db "{pos_blast_db_path}"/"{genomes}"_db -query "{BGC_path}"/"{BGC_type}"_selected_tp_genes.fasta -out "{pos_blast_results_path}"/"{genomes}".blastout -outfmt "6 qseqid sseqid pident evalue length"
    
# use pandas to concatenate all blast output tables
#df_list = []
#for outfile in os.listdir(pos_blast_results_path):
#    try:
#        blast_df = pd.read_csv(pos_blast_results_path+'/'+outfile, sep='\t', names=['qseqid', 'sseqid', 'pident', 'evalue', 'length'], index_col=None)
#        blast_df['sample'] = '.'.join(outfile.split('.')[0:2])
#        df_list.append(blast_df)
#    except EmptyDataError:
#        continue
        
# Generate a list of contaminated negative genomes        
#pos_blast_hits_df = pd.concat(df_list)
#pos_blast_hits_df.to_csv(pos_blast_path+'/blast_results_summary.csv', index=False)

In [8]:
#Use blast to find tp_gene contamination in negative samples
unique_neg_df = neg_df.drop_duplicates(subset='assembly', inplace=False)
# gets a list of length of specified amount of neg genomes
neg_genomes_list = list(unique_neg_df.iloc[:,1])

with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\n'+'Using blastn to check negative genomes for contamination'+'\n')

# makes blast databases of all individual neg genomes (easier to keep track of accession numbers than when combining)
for genomes in neg_genomes_list:
    !makeblastdb -in "{neg_genomes_path}"/"{genomes}"* -dbtype nucl -out "{neg_blast_db_path}"/"{genomes}"_db

# runs blastn search of all TP genes against all blast databases of negative genomes
for genomes in neg_genomes_list:
    !blastn -db "{neg_blast_db_path}"/"{genomes}"_db -query "{BGC_path}"/"{BGC_type}"_selected_tp_genes.fasta -out "{neg_blast_results_path}"/"{genomes}".blastout -outfmt "6 qseqid sseqid pident evalue length"

# use pandas to concatenate all blast output tables
df_list = []
for outfile in os.listdir(neg_blast_results_path):
    try:
        blast_df = pd.read_csv(neg_blast_results_path+'/'+outfile, sep='\t', names=['qseqid', 'sseqid', 'pident', 'evalue', 'length'], index_col=None)
        blast_df['sample'] = '.'.join(outfile.split('.')[0:2])
        df_list.append(blast_df)
    except EmptyDataError:
        continue
        
# Generate a list of contaminated negative genomes        
remove_df = pd.concat(df_list)
remove_df.to_csv(quality_control_path+'/blast_fn_samples.csv', index=False)
unique_remove_df = remove_df.drop_duplicates(subset='sample', inplace=False)
blast_remove_list = list(unique_remove_df.iloc[:,5])

with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\n'+'Contamination with tp_seqs:\n'+str(list(remove_df.iloc[:,0]))+'\nsequences identified in negative samples:\n'+str(blast_remove_list)+'\n\n')

print('Done')



Building a new DB, current time: 11/22/2021 11:01:46
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_007997285.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_007997285.1_ASM799728v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 26 sequences in 0.0650368 seconds.


Building a new DB, current time: 11/22/2021 11:01:47
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_004792475.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_004792475.1_ASM479247v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 1 sequences in 0.0423679 seconds.


Building a new 

Adding sequences from FASTA; added 100 sequences in 0.07307 seconds.


Building a new DB, current time: 11/22/2021 11:01:51
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_003075095.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_003075095.1_ASM307509v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 87 sequences in 0.347577 seconds.


Building a new DB, current time: 11/22/2021 11:01:52
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_004121115.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_004121115.1_ASM412111v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences f

Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 52 sequences in 0.27804 seconds.


Building a new DB, current time: 11/22/2021 11:01:57
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_900537165.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_900537165.1_ASM90053716v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 34 sequences in 0.0850661 seconds.


Building a new DB, current time: 11/22/2021 11:01:57
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_000622285.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_000622285.1_ASM62228v2_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Max

Adding sequences from FASTA; added 304 sequences in 0.073194 seconds.


Building a new DB, current time: 11/22/2021 11:02:03
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_018882205.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_018882205.1_ASM1888220v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 6 sequences in 0.022115 seconds.


Building a new DB, current time: 11/22/2021 11:02:03
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_003030385.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_003030385.1_ASM303038v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences 

Adding sequences from FASTA; added 154 sequences in 0.052654 seconds.


Building a new DB, current time: 11/22/2021 11:02:07
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_020514115.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_020514115.1_ASM2051411v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 22 sequences in 0.102928 seconds.


Building a new DB, current time: 11/22/2021 11:02:07
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_002156965.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_002156965.1_ASM215696v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences

...

Adding sequences from FASTA; added 468 sequences in 0.373298 seconds.


Building a new DB, current time: 11/22/2021 11:10:09
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_019392245.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_019392245.1_ASM1939224v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 617 sequences in 0.053421 seconds.


Building a new DB, current time: 11/22/2021 11:10:09
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_013792365.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_013792365.1_ASM1379236v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequenc

Adding sequences from FASTA; added 32 sequences in 0.0463059 seconds.


Building a new DB, current time: 11/22/2021 11:10:13
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_006380425.2_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_006380425.2_ASM638042v2_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 175 sequences in 0.0504251 seconds.


Building a new DB, current time: 11/22/2021 11:10:13
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_017351475.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_017351475.1_ASM1735147v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequenc

Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 5 sequences in 0.35971 seconds.


Building a new DB, current time: 11/22/2021 11:10:25
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_017598945.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_017598945.1_ASM1759894v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 66 sequences in 1.27918 seconds.


Building a new DB, current time: 11/22/2021 11:10:27
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_001883765.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_001883765.1_ASM188376v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximu

Adding sequences from FASTA; added 9 sequences in 1.4696 seconds.


Building a new DB, current time: 11/22/2021 11:10:46
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_003199135.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_003199135.1_ASM319913v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 52 sequences in 0.844161 seconds.


Building a new DB, current time: 11/22/2021 11:10:47
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_006352025.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_006352025.1_ASM635202v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from

Adding sequences from FASTA; added 2 sequences in 0.862695 seconds.


Building a new DB, current time: 11/22/2021 11:11:02
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_014893375.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_014893375.1_ASM1489337v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 324 sequences in 0.986794 seconds.


Building a new DB, current time: 11/22/2021 11:11:04
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_blast/databases/GCF_003349615.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_003349615.1_ASM334961v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences 

In [9]:
# Use hmmer to find tp_gene contamination in negative samples
# This is to some extent dependent on which tp genes are chosen. If fewer neg_genomes result from the decontamination
#     process than are specified by select_neg_genomes, it might be worth trying a different set of tp_genes

with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\n'+'Using hmmer to check negative genomes for contamination'+'\n\n')

# Build net alignment of tp_genes
!muscle -in "{BGC_path}"/"{BGC_type}"_selected_tp_genes.fasta -out "{neg_hmm_db_path}"/"{BGC_type}"_selected_tp_gene_alignment.fasta -loga "{BGC_path}"/report_2_generate_tp.txt

with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\n'+'Building nucleotide hmm of selected true positive genes'+'\n\n'+'Searching neg genomes with nucleotide hmm.\n\n')

# Build nucleotide based hmm of tp_genes alignment
!hmmbuild -n tp_nucl_aln --dna "{neg_hmm_db_path}"/"{BGC_type}"_tp_nucl.hmm "{neg_hmm_db_path}"/"{BGC_type}"_selected_tp_gene_alignment.fasta

# Search neg genomes with hmm
for genomes in neg_genomes_list:
    #metaBGC uses these cutoffs for all the protein hmms. This is more stringent/produces fewer results
    !nhmmer --F1 0.02 --F2 0.02 --F3 0.02 --tblout "{neg_hmm_results_path}"/"{genomes}"_hmm_result.tbl "{neg_hmm_db_path}"/"{BGC_type}"_tp_nucl.hmm "{neg_genomes_path}"/"{genomes}"*
    #This produces more results, should there be a lack of negative genomes.
#    !nhmmer --tblout "{neg_hmm_results_path}"/"{genomes}"_hmm_result.tbl "{neg_hmm_db_path}"/"{BGC_type}"_tp_nucl.hmm "{neg_genomes_path}"/"{genomes}"*

print('Done')


MUSCLE v3.8.1551 by Robert C. Edgar

http://www.drive5.com/muscle
This software is donated to the public domain.
Please cite: Edgar, R.C. Nucleic Acids Res 32(5), 1792-97.

RTX_toxin_acyltransferase_combi 10 seqs, lengths min 462, max 462, avg 462
00:00:00    15 MB(-3%)  Iter   1  100.00%  K-mer dist pass 1
00:00:00    15 MB(-3%)  Iter   1  100.00%  K-mer dist pass 2
00:00:00    20 MB(-4%)  Iter   1  100.00%  Align node       
00:00:00    20 MB(-4%)  Iter   1  100.00%  Root alignment
00:00:00    20 MB(-4%)  Iter   2  100.00%  Refine tree   
00:00:00    20 MB(-4%)  Iter   2  100.00%  Root alignment
00:00:00    20 MB(-4%)  Iter   2  100.00%  Root alignment
00:00:00    20 MB(-4%)  Iter   3  100.00%  Refine biparts
# hmmbuild :: profile HMM construction from multiple sequence alignments
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - -

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_018224955.1_ASM1822495v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/outfiles/GCF_018224955.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# 

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_000297635.1_ASM29763v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/outfiles/GCF_000297635.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - 

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_013283055.1_ASM1328305v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/outfiles/GCF_013283055.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# 

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_014705715.1_ASM1470571v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/outfiles/GCF_014705715.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# 

...

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_000310165.2_ASM31016v2_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/outfiles/GCF_000310165.2_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - 

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_002106795.1_ASM210679v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/outfiles/GCF_002106795.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# -

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_003296625.1_ASM329662v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/outfiles/GCF_003296625.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# -

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/temp_neg_genomes/GCF_002532455.1_ASM253245v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/outfiles/GCF_002532455.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# -

Done


In [10]:
# Parse hmm output
#https://stackoverflow.com/questions/62012615/convert-a-hmmer-tblout-output-to-a-pandas-dataframe

sample_list = []
id_list=[]
len_list=[]
evalue_list=[]


#Can't parse mhmmer output with biopython at the moment, so did parsing manually.
for filename in os.listdir(neg_hmm_results_path):
    samplename = '_'.join(filename.split('_')[0:2])
    with open(neg_hmm_results_path+'/'+filename) as handle:
        content = handle.readlines()
        for line in content:
            if not line.startswith('#'):
                sample_list.append(samplename)
                id_list.append(line.split()[0])
                len_list.append(int(float(line.split()[5])-float(line.split()[12])))
                evalue_list.append(float(line.split()[12]))

                
       
# Generate hit_df based on found tp_hits in neg genomes
hmm_dict = {'sample': sample_list, 'target_name': id_list, 'length': len_list,  'evalue': evalue_list}             
hit_df = pd.DataFrame.from_dict(hmm_dict)
hit_df.to_csv(neg_hmm_path+'/all_nhmmer_fn_samples.csv', index=False)

#filter hit_df by evalue cutoff
evalue_filter = hit_df['evalue'] <= hmm_evalue_cutoff
cutoff_hit_df = hit_df[evalue_filter]

#deduplicate samples
unique_hit_df = cutoff_hit_df.drop_duplicates(subset='sample', inplace=False)
unique_hit_df.to_csv(quality_control_path+'/nhmmer_elt'+str(hmm_evalue_cutoff)+'_fn_samples.csv', index=False)

# Generate a list of contaminated negative genomes with combined results from blast and hmm hits
hmm_remove_list = list(unique_hit_df.iloc[:,0])
remove_list = blast_remove_list
remove_list.extend(x for x in hmm_remove_list if x not in remove_list)

with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\n'+'Contamination with tp_seqs found in samples:\n'+str(hmm_remove_list)+'\n\n'+'Found '+str(len(remove_list))+' total samples with tp contamination in neg genomes.')

# Remove these contaminated samples from the possible pool of negative sequences
cleaned = ~unique_neg_df['assembly'].isin(remove_list)
cleaned_unique_neg_df = unique_neg_df[cleaned]

# Select a preset number of negative genomes (this could lead to fewer genomes available than selected. Handle)
selected_neg_genomes = list(cleaned_unique_neg_df.iloc[:,1])[0:select_neg_genomes]

# report block
with open(BGC_path+'/'+'report_2_generate_tp.txt', 'a') as f:
    f.write('\n\n decontaminated selected_neg_genomes are:\n')
    f.write(str(selected_neg_genomes))

for genome in selected_neg_genomes:
    print('moving negative', genome, 'to', output_neg_path)
    !mv "{neg_genomes_path}"/"{genome}"* "{output_neg_path}"
    
print('Done')

moving negative GCF_007997285.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_001529365.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_000297635.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_003075095.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_002964545.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_000943565.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_002150505.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_000331225.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving n

moving negative GCF_014076925.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_002872475.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_001681955.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_008711455.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_001999595.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_003410035.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_002573675.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_010669085.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving n

moving negative GCF_004921245.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_020524705.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_002101785.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_002893215.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_002140155.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_017638545.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_000463345.2 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving negative GCF_001752425.1 to /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/neg_genomes
moving n

In [11]:
# To confirm, run blast on all samples selected as pos genomes

# makes blast databases of all individual neg genomes (easier to keep track of accession numbers than when combining)
for genomes in selected_tp_genomes:
    !makeblastdb -in "{output_pos_path}"/"{genomes}"* -dbtype nucl -out "{pos_blast_db_path}"/"{genomes}"_db

for genomes in selected_tp_genomes:
    !blastn -db "{pos_blast_db_path}"/"{genomes}"_db -query "{BGC_path}"/"{BGC_type}"_selected_tp_genes.fasta -out "{pos_blast_results_path}"/"{genomes}".blastout -outfmt "6 qseqid sseqid pident evalue length"
    
# use pandas to concatenate all blast output tables
df_list = []
for outfile in os.listdir(pos_blast_results_path):
    try:
        blast_df = pd.read_csv(pos_blast_results_path+'/'+outfile, sep='\t', names=['qseqid', 'sseqid', 'pident', 'evalue', 'length'], index_col=None)
        blast_df['sample'] = '.'.join(outfile.split('.')[0:2])
        df_list.append(blast_df)
    except EmptyDataError:
        continue
        
# Generate a list of contaminated negative genomes        
pos_blast_hits_df = pd.concat(df_list)
pos_blast_hits_df.to_csv(pos_blast_path+'/blast_results_summary.csv', index=False)



Building a new DB, current time: 11/22/2021 11:37:47
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_blast/databases/GCF_012275045.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_012275045.1_ASM1227504v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 2 sequences in 1.74775 seconds.


Building a new DB, current time: 11/22/2021 11:37:50
New DB name:   /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_blast/databases/GCF_013357805.1_db
New DB title:  /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_013357805.1_ASM1335780v1_genomic.fna
Sequence type: Nucleotide
Keep MBits: T
Maximum file size: 1000000000B
Adding sequences from FASTA; added 3 sequences in 0.909324 seconds.


Building a new DB, current 

In [12]:
# To confirm, run nhmmer on all samples selected as pos genomes


# Search neg genomes with hmm
for genomes in selected_tp_genomes:
    !nhmmer --F1 0.02 --F2 0.02 --F3 0.02 --tblout "{pos_hmm_results_path}"/"{genomes}"_hmm_result.tbl "{neg_hmm_db_path}"/"{BGC_type}"_tp_nucl.hmm "{output_pos_path}"/"{genomes}"*

sample_list = []
id_list=[]
evalue_list=[]
len_list = []

#Can't parse mhmmer output with biopython at the moment, so did parsing manually.
for filename in os.listdir(pos_hmm_results_path):
    samplename = '_'.join(filename.split('_')[0:2])
    with open(pos_hmm_results_path+'/'+filename) as handle:
        content = handle.readlines()
        for line in content:
            if not line.startswith('#'):
                sample_list.append(samplename)
                id_list.append(line.split()[0])
                len_list.append(int(float(line.split()[5])-float(line.split()[12])))
                evalue_list.append(float(line.split()[12]))

                
       
# Generate hit_df based on found tp_hits in neg genomes
hmm_dict = {'sample': sample_list, 'target_name': id_list, 'length': len_list, 'evalue': evalue_list}             
hit_df = pd.DataFrame.from_dict(hmm_dict)
hit_df.to_csv(pos_hmm_path+'/nhmmer_all_pos_samples.csv', index=False)

#deduplicate samples
unique_hit_df = hit_df.drop_duplicates(subset='sample', inplace=False)
unique_hit_df.to_csv(pos_hmm_path+'/nhmmer_unique_pos_samples.csv', index=False)

print('Done')

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_012275045.1_ASM1227504v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_hmm/results/GCF_012275045.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - - - 

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_013357805.1_ASM1335780v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_hmm/results/GCF_013357805.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - - - 

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_013357665.1_ASM1335766v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_hmm/results/GCF_013357665.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - - - 

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_013357885.1_ASM1335788v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_hmm/results/GCF_013357885.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - - - 

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_002119525.1_ASM211952v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_hmm/results/GCF_002119525.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - - - -

...

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_008369605.1_ASM836960v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_hmm/results/GCF_008369605.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - - - -

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_001455365.1_ASM145536v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_hmm/results/GCF_001455365.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - - - -

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_001895965.1_ASM189596v1_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_hmm/results/GCF_001895965.1_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - - - -

# nhmmer :: search a DNA model, alignment, or sequence against a DNA database
# HMMER 3.3 (Nov 2019); http://hmmer.org/
# Copyright (C) 2019 Howard Hughes Medical Institute.
# Freely distributed under the BSD open source license.
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# query file:                      /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/neg_hmm/queries/RTX_toxin_acyltransferase_combined_tp_nucl.hmm
# target sequence database:        /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/pos_genomes/GCF_001908435.2_ASM190843v2_genomic.fna
# hits tabular output:             /media/manu/RiPP_Prioritiser/RTX_toxin_acyltransferase_combined/base_genomes/quality_control/pos_hmm/results/GCF_001908435.2_hmm_result.tbl
# SSV filter P threshold:       <= 0.02
# Vit filter P threshold:       <= 0.02
# Fwd filter P threshold:       <= 0.02
# number of worker threads:        2
# - - - -

Done
